# MIR Project

<div dir="rtl">
    این دفترچه مربوط به نسخه ی فارسی جستجوگر است. پیش از اجرا لازم است که کتابخانه های زیر را نصب کنید.
</div>

In [36]:
from __future__ import unicode_literals
from hazm import *
import re
import xml.etree.ElementTree as ET
import pickle
import math
import numpy as np
import sys
import os
from struct import pack, unpack

# بخش اول: پیش پردازش اولیه

<div dir="rtl">
    تابع زیر تگ های مهم فایل xml را استخراج میکند. پس از مشاهده ی ساختار فایل سه تگ title, text حائز اهمیت تر از سایر تگ ها بودند برای همین در این تابع فقط این دو تگ را استخراج میکنیم.
<br>
    در نهایت خروجی این تابع یک آرایه از متون مربوط به صفحات است که هر عنصر آن متن یک صفحه را به صورت دیکشنری مشخص میکند و در آن عنوان و متن جدا از هم وجود دارند.
<br>
</div>

In [37]:
def parse_XML(filename):
    tree = ET.parse(filename)
    root = tree.getroot()
    pages = []
    for page in root.findall("{http://www.mediawiki.org/xml/export-0.10/}page"):
        p_text = {}
        for child in page.iter("{http://www.mediawiki.org/xml/export-0.10/}title"):
            p_text['title'] = child.text
        for child in page.iter("{http://www.mediawiki.org/xml/export-0.10/}text"):
            p_text['text'] = child.text
        pages.append(p_text)   
    return pages

<div dir="rtl">
    در تابع زیر کار پیش پردازش اولیه متن را انجام میدهیم. این تابع به عنوان ورودی آدرس یک فایل که حاوی داده های به فرمتxml است را دریافت میکند.علاوه بر این سه مقدار:
    <br> PUNC_FLAG
    <br> STEM_FLAG
    <br> STWD_FLAG
    <br>
    را میگیرد که نیازمندی های کاربر را مشخص میکند و مشخص میکند آیا کاربر میخواهد که علائم نگارشی یا کلمات stopحذف شوند یا نه. یا میخواهد که کلمات به ریشه برده شوند یا خیر.
    <br>
    برای نرمالسازی و tokenize کردن متن از توابع آماده ی کتابخانه ی هضم استفاده میکنیم و برای حذف stop word ها از معیار تکرار کلمات در تمامی مستندات استفاده میکنیم. به این صورت که اگر کلمه ای در ۵۰ درصد مستندات وجود دارد، آن را حذف میکنیم.
    (این عدد به صورت تجربی و با مشاهده ی تست آن روی تعداد مختلف مستندات قرار داده شده است. عدد رایج آن ۸۵ درصد است ما در این مجموعه داده کلمات خیلی کمی درصد بالای ۶۰ را دارند. به همین خاطر به صورت تجربی عدد ۵۰ درصد را انتخاب کرده ایم.)
    
   </div>

In [38]:
def retrieve_stop_words(word_index, n):
    stop_words = []
    for key, value in word_index.items():
        normalized_df = len(value)/n
        if normalized_df >= 0.5:
            stop_words.append(key)
    with open('retrieved_stopwords.pickle', 'wb') as handle:
        pickle.dump(stop_words, handle, protocol = pickle.HIGHEST_PROTOCOL)
    return stop_words

In [39]:
def prepare_text_per(filename, PUNC_FLAG, STEM_FLAG, STWD_FLAG):
    pages = parse_XML(filename)
    main_page = []
    word_index = {}
    word_frq = {}
    for m in range(len(pages)):
        #removing all puctuations
        if(PUNC_FLAG):
            title = re.sub(r"[\[,.;:\-@#}?؟{٪٬*!)%’(&$<_>/'»«|+=.\]]+\ *", " ", pages[m].get('title'))
            text = re.sub(r"[\[,.;:\-@#}?؟{٪٬*!)%’(&$<_>/'»«|+=.\]]+\ *", " ", pages[m].get('text'))
        else:
            title = pages[m].get('title')
            text = pages[m].get('text')
        #removing all english letters and numbers
        new_title = ""
        new_text = ""
        for i in title.split(' '):
            if i.isascii() == False and i.isdigit() == False:
                new_title += i + ' '
        for i in text.split(' '):
            if i.isascii() == False and i.isdigit() == False:
                new_text += i + ' '
                
        title = new_title
        text = new_text
        main_page += [new_title + '\n' + new_text]
        normalizer = Normalizer()
        title = normalizer.normalize(title)
        text = normalizer.normalize(text)
        tokenizer = WordTokenizer()
        title = tokenizer.tokenize(title)
        text = tokenizer.tokenize(text)
        new_title = []
        new_text = []
        if(STEM_FLAG):
            stemmer = Stemmer()
            for t in title:
                t1 = stemmer.stem(t)
                new_title += [t1]
                if t not in word_frq.keys():
                    word_frq[t] = 1
                else:
                    word_frq[t] += 1
                if t not in word_index.keys():
                    word_index[t] = set([m])
                else:
                    word_index[t].add(m)
            for t in text:
                t1 = stemmer.stem(t)
                new_text += [t1]
                if t not in word_frq.keys():
                    word_frq[t] = 1
                else:
                    word_frq[t] += 1
                if t not in word_index.keys():
                    word_index[t] = set([m])
                else:
                    word_index[t].add(m)
            pages[m].update(title=new_title, text=new_text)
            
        else:
            for t in title:
                if t not in word_index.keys():
                    word_index[t] = set([m])
                else:
                    word_index[t].add(m)
                new_title += [t]
            for t in text:
                if t not in word_index.keys():
                    word_index[t] = set([m])
                else:
                    word_index[t].add(m)
                new_text += [t]
            pages[m].update(title=new_title, text=new_text)
    
    print("the list of most frequent words:(before deleting stop words)")
    pops = sorted(word_frq, key=word_frq.get, reverse=True)
    print(pops[:20])
    if(STWD_FLAG):
        #if the new document is added here
        if(len(pages) == 1):
            with open('retrieved_stopwords.pickle', 'rb') as handle:
                stop_words = pickle.load(handle)
        else:
            stop_words = retrieve_stop_words(word_index, len(pages))
            #print(stop_words)
    print("the list of most frequent words:(after deleting stop words)")
    pops = [w for w in pops if w not in stop_words]
    print(pops[:20])
    for m in range(len(pages)):
        filtered_title = [w for w in pages[m].get('title') if not w in stop_words]
        filtered_text = [w for w in pages[m].get('text') if not w in stop_words]
        pages[m].update(title=filtered_title, text=filtered_text)
    
    return pages, main_page

## تست بخش اول پیش پردازش 

<div dir="rtl">
    کد زیر برای امتحان و تست تابع پیش پردازش نوشته شده است و در نهایت مجموعه کلمات را به تفکیک مستندات و zone آنها خروجی میدهد. همچنین این تابع کلمات پرتکرار را قبل و بعد از حذف ایست واژه ها چاپ میکند. (با توجه به اینکه ایست واژه ها با معیار دیگری  تعیین شده اند مجموعه کلمات پرتکرار قبل و بعد از حذف آنها متفاوت است.)
</div>

In [40]:
if(input("Do you want stemming?[T/F]") == 'T'): 
    stfl = True
else: stfl = False
if(input("Do you want stop word removal?[T/F]") == 'T'): 
    stwdfl = True
else: stwdfl = False
if(input("Do you want punctuation?[T/F]") == 'T'): 
    puncfl = True
else: puncfl = False
preprocessed , main_docs= prepare_text_per("data/persian_test2.xml",puncfl, stfl, stwdfl)

Do you want stemming?[T/F]T
Do you want stop word removal?[T/F]T
Do you want punctuation?[T/F]T
the list of most frequent words:(before deleting stop words)
['و', '،', 'در', 'از', 'به', 'که', 'این', 'را', 'است', 'با', 'آن', 'سال', 'رده', 'ایران', 'بر', 'تاریخ', 'برای', 'کشور', 'استان', 'شهر']
the list of most frequent words:(after deleting stop words)
['را', 'با', 'سال', 'ایران', 'بر', 'تاریخ', 'برای', 'استان', 'شهر', 'زبان', 'یک', 'دو', 'نیز', 'تا', 'عنوان', 'آمریکا', 'آلبانی', 'یا', 'خود', 'دارد']


#  بخش دوم: نمایه سازی

<div dir='rtl'>
    در این بخش برای ذخیره سازی بایگرام ها از کتابخانه ی pickle استفاده شده است که در ابتدای این گزارش import شده. علاوه بر این برای حذف مستند نیازمندیم تا آرایه ای در نظر بگیریم که در ابتدای این بخش آن را تعریف میکنیم.
</div>

In [41]:
n = len(main_docs)
deleted_doc = [False for i in range(n)]

<div dir='rtl'>
    در این بخش تابع زیر مجموعه ی positional index را با در نظر گرفتن zone کلمات میسازد. برای این کار با حرکت روی هر مستند کلمات مربوط به آن را با ذخیره کردن مکان آنها به خروجی نهایی اضافه میکند.
    </div>

In [42]:
def positional_index_dictionary_maker(docs, deleted_doc):
    positional_index = {}
    for i in range(len(docs)):
        if deleted_doc[i] ==False:
            title = docs[i].get('title')
            text = docs[i].get('text')
            index_counter = 0
            for word in title:
                if word in positional_index:
                    newTermInDoc = True
                    for doc_elm in positional_index[word]:
                        if i == doc_elm[0]:
                            doc_elm[1].get('title').append(index_counter)
                            newTermInDoc = False
                            break
                    if newTermInDoc == True:
                        positional_index[word].append((i,{'title': [index_counter]}))
                else: positional_index[word] = [(i,{'title': [index_counter]})]
                index_counter += 1
            index_counter = 0
            for word in text:
                if word in positional_index:
                    newTermInDoc = True
                    for doc_elm in positional_index[word]:
                        if i == doc_elm[0]:
                            if('text' in doc_elm[1].keys()):
                                doc_elm[1]['text'].append(index_counter)
                            else:
                                doc_elm[1]['text'] = []
                                doc_elm[1]['text'].append(index_counter)
                            newTermInDoc = False
                            break
                    #if word is in dict but the doc isnt
                    if newTermInDoc == True:
                        positional_index[word].append((i,{'text': [index_counter]}))
                #if there is word hsa not been saved in dict
                else: positional_index[word] = [(i,{'text': [index_counter]})]
                index_counter += 1
    return positional_index

<div dir='rtl'>
    حال این تابع را روی مجموعه مستندات پیش پردازش شده ی بخش قبل اجرا میکنیم و همانطور که در خروجی کد زیر هست این تایع positional index مربوط به مستندات را به درستی میسازد. خروجی این تابع، یک دیکشنری است که ایندکس‌های مربوط به هر term را ذخیره کرده است.
    </div>

In [43]:
positions = positional_index_dictionary_maker(preprocessed, deleted_doc)
print("The total posting list is: ")
for key, value in positions.items():
    if 0 in value[0]:
        print(key)
        print(value)
len(main_docs)

The total posting list is: 
باز
[(0, {'title': [0], 'text': [35, 37, 48, 52, 54]}), (12, {'text': [1961]}), (16, {'text': [513]}), (19, {'text': [1517]}), (25, {'text': [1003, 1116, 1677, 2391]}), (29, {'text': [786]}), (30, {'text': [267, 624]}), (36, {'text': [278, 592, 5618, 9121, 10485, 10805]}), (39, {'text': [2179, 2653]}), (40, {'text': [343]}), (42, {'text': [307, 636, 772, 775]}), (44, {'text': [3581]}), (45, {'text': [38]}), (47, {'text': [178]}), (52, {'text': [979]}), (54, {'text': [245]}), (56, {'text': [40, 259, 1124, 1217]}), (64, {'text': [542, 886]}), (65, {'text': [1259, 2497]}), (71, {'text': [2906]}), (72, {'text': [244, 1078]}), (112, {'text': [1229]}), (125, {'text': [735]}), (130, {'text': [271]}), (140, {'text': [181]}), (146, {'text': [1136, 1146, 1189, 1201]}), (149, {'text': [650]}), (150, {'text': [362]}), (162, {'text': [1499, 2302, 3553, 4080]})]
فکر
[(0, {'title': [1], 'text': [1, 10, 17, 26, 59]}), (36, {'text': [4320, 4430]}), (39, {'text': [1663]}), (4

167

<div dir="rtl">حال برای اضافه کردن یک مستند به مجموع مستندات ابتدا آدرس آن را میگیریم و پیش پردازش های لازم را روی آن انجام میدهیم و سپس آن را به نمایه های قبلی اضافه میکنیم. </div>

In [44]:
def add_document(filename,PUNC_FLAG, STEM_FLAG, STWD_FLAG, 
                             positional_index, resault ,deleted_doc, n, docs,main_docs):
    doc , main_doc= prepare_text_per(filename, PUNC_FLAG, STEM_FLAG, STWD_FLAG)
    docs.extend(doc)
    main_docs.extend(main_doc)
    deleted_doc.append(False)
    title = doc[0].get('title')
    text = doc[0].get('text')
    i = n
    index_counter = 0
    for word in title:
        if word in positional_index:
            newTermInDoc = True
            for doc_elm in positional_index[word]:
                if i == doc_elm[0]:
                    doc_elm[1].get('title').append(index_counter)
                    newTermInDoc = False
                    break
            if newTermInDoc == True:
                positional_index[word].append((i,{'title': [index_counter]}))
        else: positional_index[word] = [(i,{'title': [index_counter]})]
        index_counter += 1
    index_counter = 0
    for word in text:
        if word in positional_index:
            newTermInDoc = True
            for doc_elm in positional_index[word]:
                if i == doc_elm[0]:
                    if('text' in doc_elm[1].keys()):
                        doc_elm[1]['text'].append(index_counter)
                    else:
                        doc_elm[1]['text'] = []
                        doc_elm[1]['text'].append(index_counter)
                    newTermInDoc = False
                    break
            #if word is in dict but the doc isnt
            if newTermInDoc == True:
                positional_index[word].append((i,{'text': [index_counter]}))
        #if there is word hsa not been saved in dict
        else: positional_index[word] = [(i,{'text': [index_counter]})]
        index_counter += 1
        
    doc = doc[0].get('title')+doc[0].get('text')
    for term in doc:
        chars = ['$']
        for i in range(len(term)):
            chars.append(term[i])
        chars.append('$')
        for i in range(len(chars) - 1):
            current = chars[i] + chars[i + 1]

            if current in resault:
                newTermInDoc = True
                for doc_elm in resault[current]:
                    if term == doc_elm:
                        newTermInDoc = False
                        break
                if newTermInDoc == True:
                    resault[current].append(term)
            else: resault[current] = [term]
    return positional_index, resault

<div dir="rtl">حال برای حذف کردن یک مستند از مجموعه مستندات کافی است که خانه ی docID مربوط به آن مستند true شود و در درون positional index در صورتی نمایه سازی انجام خواهد شد که خانه ی مربوطه false باشد. بعد از صدا کردن این تابع، باید positional index و bigram را دوباره فراخوانی کنیم که هنگام تست این تابع انجام شده‌است.</div>

In [117]:
def delete_document(docID , deleted_doc, main_docs, docs):
    deleted_doc[docID]=True
    return deleted_doc

<div dir="rtl">حال به محاسبه ی bigram میپردازیم و در صورتی که داکیومنتی حذف نشده بود کلمات آن به شکل bigram در یک دیکشنری ذخیره میشوند.</div>

In [46]:
def bigram_dictionary_maker(docs,deleted_doc):
    resault = {}
    count =0
    for doc in docs:
        if deleted_doc[count]==False:
            for term in doc:
                chars = ['$']
                for i in range(len(term)):
                    chars.append(term[i])
                chars.append('$')
                for i in range(len(chars) - 1):
                    current = chars[i] + chars[i + 1]

                    if current in resault:
                        newTermInDoc = True
                        for doc_elm in resault[current]:
                            if term == doc_elm:
                                newTermInDoc = False
                                break
                        if newTermInDoc == True:
                            resault[current].append(term)
                    else: resault[current] = [term]
        count+=1                  
    return resault

<div dir="rtl">حال title و text ها را روی هم ریخته ایم تا بتوانیم bigram را روی آنها اجرا کنیم.</div>

In [47]:
documents = []
for i in range(len(preprocessed)):
    documents += [preprocessed[i].get('title') + preprocessed[i].get('text')]
bigrams = bigram_dictionary_maker(documents,deleted_doc)

<div dir="rtl">اکنون برای مثال برای «قت» این تابع را فراخوانی می‌کنیم و تنایج آن را می‌بینیم.</div>

In [49]:
bigrams.get('قت')

['مقتضا',
 'اقتصاد',
 'قتل',
 'اقتدار',
 'مقتدر',
 'آقتائو',
 'قتال',
 'بقتل',
 'اقتباس',
 'وقت',
 'قتیله',
 'حقیقتا',
 'اقتباس\u200cشده',
 'وبقتل']

<div dir="rtl">حال در صورت اضافه کردن مستندی به مجموعه مستندات term های مستند جدید را به bigram تبدیل کرده و به bigram های پیشین اضافه میکنیم.</div>

<div dir='rtl'>
    در تابع زیر بایگرام ساخته شده را در یک فایل ذخیره میکنیم 
    </div>

In [50]:
def bigram_saver(my_dict, name):
    with open(name, 'wb') as handle:
        pickle.dump(my_dict, handle, protocol = pickle.HIGHEST_PROTOCOL)

In [51]:
bigram_saver(bigrams, 'bigram.pickle')

<div dir='rtl'>
و با استفاده از تابع زیر میتوان هر زمان که لازم بود آنها را از فایل لود کنیم
</div>

In [52]:
def bigram_loader(name):
    with open(name, 'rb') as handle:
        resault = pickle.load(handle)
    return resault

<div dir='rtl'>
    با استفاده از تابع زیر میتوانیم نمایه های ساخته شده را ذخیره کنیم.
    </div>

In [53]:
def positional_index_saver(my_dict, name):
    with open(name, 'wb') as handle:
        pickle.dump(my_dict, handle, protocol = pickle.HIGHEST_PROTOCOL)

In [54]:
positional_index_saver(positions, 'positional_index.pickle')

<div dir='rtl'>
    برای خواندن نمایه ها از فایل هم از تابع زیر استفاده میکنیم.
    </div>

In [55]:
def positional_index_loader(name):
    with open(name, 'rb') as handle:
        resault = pickle.load(handle)
    return resault

### تست بخش دوم

In [56]:
print("please enter a word that you want to know its positional posting list:")
term = input()
for word in positions:
    if word == term:
        print(positions[word])

please enter a word that you want to know its positional posting list:
شیراز
[(6, {'text': [2034]}), (12, {'text': [15]}), (29, {'text': [763]}), (36, {'text': [5967, 7177]}), (52, {'text': [554, 1015, 5179, 5320, 5638, 5671, 5759, 5764, 5767, 5841, 6234, 7515]}), (53, {'text': [2981]}), (72, {'text': [2603]}), (109, {'text': [316]}), (126, {'text': [2084]}), (128, {'text': [524]}), (130, {'text': [7]})]


In [57]:
print("Please enter a word and documentID that you want to know its position:")
term=input()
docID = int(input())
for word in positions:
    if word == term:
        for j in range(len(positions[word])):
            if positions[word][j][0] == docID:
                print(positions[word][j][1])

Please enter a word and documentID that you want to know its position:
شیراز
52
{'text': [554, 1015, 5179, 5320, 5638, 5671, 5759, 5764, 5767, 5841, 6234, 7515]}


In [59]:
print("please enter a bigram to see the terms that contain it:")
bigram = input()
for bi in bigrams:
    if bi == bigram:
        print(bigrams[bi])

please enter a bigram to see the terms that contain it:
مس
['مساح', 'مسافر', 'زمستان', 'مسیح', 'مسکون', 'مسدور', 'تلمس', 'مستقل', 'تلمسن', 'مسل', 'مسلط', 'مستعمره', 'مسجد', 'مساجد', 'مسلمان', 'المستعمر', 'همسران', 'مساحت', 'المسلمین', 'اخوان\u200cالمسلمین', 'مسئول', 'مسافربر', 'الخمس', 'غدامس', 'مسلاته', 'مسیر', 'مسینا', 'مسیر۲', 'هرمس', 'همسایه', 'مسیب\u200cبن', 'مسعود', 'مسکن', 'مستقیما', 'زمس', 'همسایگ', 'مستقر', 'مسلح', 'تغییرمسیر', 'همسر', 'مسؤول', 'مستعمره\u200cنشین', 'کریسمس', 'مسروقه', 'مستند', 'زرمس', 'درمسیر', 'مسلک', 'مسوولین', 'مسئولین', 'مساف', 'مسئله', 'مسائل', 'مسلحانه', 'مسالمت\u200cآمیز', 'مستضعفین', 'مستق', 'امسال', 'مسئله\u200cدار', 'مستضعف', 'مستکبر', 'مستعمر', 'آمستردا', 'فیلمساز', 'آرمسترانگ', 'مسابق', 'مس', 'مسبب', 'گرمسیر', 'مستحک', 'مستلز', 'همسرا', 'حرمسرا', 'مسر', 'مستوف', 'نامسلمان', 'مستمر', 'شمسیه', 'شمس', 'مسئولیت', 'مسلمین', 'مسیلمه', 'مستعمل', 'همسان', 'خمسه', 'مسترقه', 'مستطیل', 'همسایه\u200cاس', 'چندهمسر', 'مستقیم', 'مستشرق', 'مساو', 'مستثن', 'مسئولان

In [60]:
print("Please enter the address of a document that you want to add to other documents:")
address = input()
print(len(main_docs))
positions, bigrams = add_document(address ,True, True, True,
                                     positions,bigrams, deleted_doc, n, preprocessed, main_docs)
print(len(main_docs))

Please enter the address of a document that you want to add to other documents:
data/added_doc.xml
167
the list of most frequent words:(before deleting stop words)
['به', '،', 'ویکی\u200cپدیا', 'در', 'که', 'شما', 'را', 'از', 'کاربری', 'و', 'این', 'حساب', 'با', 'برای', 'آن', 'صفحهٔ', 'یک', 'سامانه', 'کاربران', 'ویرایش']
the list of most frequent words:(after deleting stop words)
['ویکی\u200cپدیا', 'شما', 'را', 'کاربری', 'حساب', 'با', 'برای', 'صفحهٔ', 'یک', 'سامانه', 'کاربران', 'ویرایش', 'دسترسی', 'خود', 'وارد', 'ویکی', 'کنید', 'کنند', 'کردن', 'آدرس']
168


In [61]:
type(positions)

dict

In [110]:
print("please enter the documentID that you want to delete it:")
documentID = int(input())
deleted_doc = delete_document(documentID , deleted_doc,main_docs, preprocessed)
bigrams = bigram_dictionary_maker(documents,deleted_doc)
positions = positional_index_dictionary_maker(preprocessed, deleted_doc)

please enter the documentID that you want to delete it:
0


In [116]:
for key, value in positions.items():
    print(key)
    print(value)

شهرس
[(1, {'title': [0], 'text': [1, 4, 47, 138, 201, 262, 274, 285, 300, 541, 642]}), (10, {'text': [18, 19]}), (12, {'text': [2941]}), (16, {'text': [740, 783, 831]}), (26, {'text': [142]}), (28, {'text': [60]}), (29, {'text': [217, 308, 337]}), (39, {'text': [5595]}), (43, {'text': [1831, 1877]}), (45, {'text': [16, 28]}), (52, {'text': [547]}), (62, {'text': [24, 176, 185, 330, 332, 833, 1305, 1427, 1447, 1544, 1779, 2073, 2288, 2305, 2321, 2446, 2471, 2490, 2502]}), (66, {'text': [27]}), (67, {'text': [32]}), (69, {'text': [23]}), (70, {'text': [29]}), (73, {'text': [47]}), (88, {'text': [56]}), (95, {'text': [12]}), (97, {'text': [10]}), (98, {'text': [10]}), (102, {'text': [43]}), (104, {'text': [106, 114]}), (128, {'text': [26]}), (161, {'title': [0], 'text': [1, 4, 44, 55, 65, 70, 78, 97, 156, 175, 187, 210, 240, 256, 261, 279, 284, 304, 325, 636, 643, 649, 651]}), (163, {'text': [16, 21, 53, 136, 258, 270, 275, 277, 281]}), (164, {'title': [0], 'text': [0]}), (166, {'title': 

استخوان
[(6, {'text': [135]})]
ابزار
[(6, {'text': [136]}), (12, {'text': [4759]}), (19, {'text': [322, 1121]}), (36, {'text': [1713]}), (41, {'text': [507]}), (64, {'text': [980, 992, 1718, 1812]}), (68, {'text': [519]}), (72, {'text': [435]}), (130, {'text': [239]}), (147, {'text': [1583, 2437]}), (149, {'text': [97]}), (150, {'text': [429]}), (167, {'text': [1062, 1063]})]
کندوکاو
[(6, {'text': [137]})]
باستان‌شناس
[(6, {'text': [138]}), (20, {'text': [312]}), (24, {'text': [45, 157]}), (31, {'text': [306]}), (52, {'text': [880, 1269, 1384, 5474, 5587, 7919]}), (57, {'text': [475]})]
قفصه
[(6, {'text': [140, 959, 2367]})]
کاپسا
[(6, {'text': [141]})]
باستان
[(6, {'text': [142]}), (9, {'text': [244]}), (10, {'text': [101, 146]}), (11, {'text': [137]}), (12, {'text': [645, 829, 2654, 2799, 4986]}), (20, {'text': [70]}), (24, {'text': [51, 213]}), (30, {'text': [224]}), (43, {'text': [651]}), (45, {'text': [45]}), (52, {'text': [168, 185, 5175, 5323, 5344, 7538, 7903, 7939]}), (53, {'t

فراورده
[(6, {'text': [1486]}), (62, {'text': [1546]}), (72, {'text': [2227]})]
انرژ
[(6, {'text': [1491]}), (39, {'text': [3318, 3845, 3854, 4140, 4147]}), (43, {'text': [1081, 1085]}), (44, {'text': [2259, 2845, 2865, 3058, 3079, 3753, 3759]}), (51, {'text': [99, 310, 420, 504, 592]}), (57, {'text': [708]}), (60, {'text': [60, 1074, 1102, 1105]}), (63, {'text': [17]}), (65, {'text': [1359, 1888, 1895, 1916, 2731]}), (71, {'text': [2736, 2741, 2776, 3886]}), (72, {'text': [238]}), (147, {'text': [1610, 1678, 1705]}), (149, {'text': [406, 413]})]
هم‌چون
[(6, {'text': [1492, 1918]}), (72, {'text': [2068]}), (162, {'text': [258]})]
گاز
[(6, {'text': [1494]}), (8, {'text': [1866]}), (43, {'text': [2021]}), (57, {'text': [731, 740]}), (60, {'text': [770, 776, 783, 968]}), (65, {'text': [1397, 1414]}), (71, {'text': [2932, 2944, 2951, 2956]}), (119, {'text': [72]}), (147, {'text': [396, 584, 628, 872, 1258, 1384, 1430, 1435, 1773, 2678, 2959]}), (149, {'text': [1531, 1542, 1557, 1581, 1605,

جماهیر
[(8, {'text': [650, 1356, 1431]}), (12, {'text': [2676]}), (21, {'text': [377]}), (39, {'text': [561, 2194, 2198]}), (53, {'text': [1934, 2011]}), (146, {'text': [907]})]
سوسیالیست
[(8, {'text': [652, 1358, 2141]}), (39, {'text': [563, 2196]}), (53, {'text': [2013]}), (72, {'text': [1654]}), (141, {'text': [518, 520]})]
صنایع
[(8, {'text': [658]}), (12, {'text': [572]}), (36, {'text': [1539]}), (39, {'text': [4055, 4059, 4086, 4089, 4109, 4116, 5635]}), (40, {'text': [845]}), (41, {'text': [36, 511, 513]}), (43, {'text': [1931, 1946, 1949, 1951, 1960, 1979]}), (52, {'text': [1052]}), (62, {'text': [1499, 1502, 1728]}), (65, {'text': [1667, 3981]}), (71, {'text': [2540, 3192, 3820, 3847]}), (72, {'text': [2119]}), (79, {'text': [74]}), (146, {'text': [1087]}), (149, {'text': [1217, 2037]})]
عرصه
[(8, {'text': [662]}), (13, {'text': [280]}), (36, {'text': [3623, 10046]}), (39, {'text': [5264]}), (43, {'text': [389, 462, 789]}), (71, {'text': [1784]}), (72, {'text': [1797]})]
رویکر

[(12, {'text': [126, 550, 3847, 3902]}), (56, {'text': [535, 594, 894, 934, 938, 950, 957, 1073, 1118, 1121, 1164, 1169, 1171, 1179, 1184, 1189, 1625]}), (125, {'text': [814]}), (126, {'text': [1418]}), (146, {'text': [1223, 1236]})]
مزدیسنا
[(12, {'text': [127]}), (15, {'text': [141, 144]}), (53, {'text': [3957]}), (56, {'text': [1108]})]
اقوا
[(12, {'text': [131, 155, 1815, 1823, 2271, 4709, 4952, 4954, 4956, 4958, 4961, 4963, 4965, 4967, 4969]}), (25, {'text': [1386]}), (27, {'text': [58]}), (28, {'text': [115]}), (31, {'text': [55]}), (39, {'text': [1602]}), (53, {'text': [2564, 2781, 4226, 4265]}), (72, {'text': [288]}), (133, {'text': [110, 112]}), (134, {'text': [65]})]
تال
[(12, {'text': [135]}), (130, {'text': [412]})]
لر
[(12, {'text': [137, 1296, 1361]}), (44, {'text': [1433]}), (62, {'text': [64, 220]}), (166, {'text': [61, 157, 164, 182, 187, 197]})]
فارسی‌زبان
[(12, {'text': [139]}), (148, {'text': [400]})]
بلوچ
[(12, {'text': [142, 1669, 1849, 4755]}), (25, {'text': [476

...

[(109, {'text': [1109]})]
برگن
[(109, {'text': [1110]})]
ترومسو
[(109, {'text': [1111]})]
تروند
[(109, {'text': [1112]})]
فردریک‌استاد
[(109, {'text': [1113]})]
کریستیان‌ساند
[(109, {'text': [1114]})]
کریستیان‌سوند
[(109, {'text': [1115]})]
درامن
[(109, {'text': [1116]})]
ساندنس
[(109, {'text': [1117]})]
مولده
[(109, {'text': [1118]})]
نیام
[(109, {'text': [1121]})]
نیجریه
[(109, {'text': [1123]})]
آبوجا
[(109, {'text': [1124]})]
لاگوس
[(109, {'text': [1125]})]
نیکاراگوآ
[(109, {'text': [1127]})]
ماناگوا
[(109, {'text': [1128]})]
لئون
[(109, {'text': [1129]})]
واتیک
[(109, {'text': [1131, 1132, 1134]})]
وانواتو
[(109, {'text': [1136]})]
پورت‌ویلا
[(109, {'text': [1137]})]
کاراکاس
[(109, {'text': [1140]})]
کریستوبال
[(109, {'text': [1142]})]
باریناس
[(109, {'text': [1144]})]
والرا
[(109, {'text': [1145]})]
آکاریگوآ
[(109, {'text': [1146]})]
بارکیزیمتو
[(109, {'text': [1148]})]
کابیماس
[(109, {'text': [1149]})]
ماراکایبو
[(109, {'text': [1150]})]
ماراکا
[(109, {'text': [1151]})]
باروتا
[

[(125, {'text': [627]}), (128, {'text': [445, 454]})]
اجاره
[(125, {'text': [638]})]
کلف
[(125, {'text': [647]})]
گزید
[(125, {'text': [653]})]
گریب
[(125, {'text': [671]})]
لطمه
[(125, {'text': [684]}), (126, {'text': [958]})]
شرمنده
[(125, {'text': [688]})]
غفل
[(125, {'text': [705]}), (126, {'text': [1193]})]
گذرانده
[(125, {'text': [706]})]
زندگان
[(125, {'text': [707]}), (162, {'text': [44, 679]})]
دوتا
[(125, {'text': [715]})]
وفا
[(125, {'text': [719]})]
دریافته
[(125, {'text': [723]})]
مکاتبه
[(125, {'text': [730]})]
سردین
[(125, {'text': [742]})]
جواب
[(125, {'text': [754, 1071]})]
نگذ
[(125, {'text': [758]})]
پش
[(125, {'text': [761]})]
زودرس
[(125, {'text': [776]})]
جیر
[(125, {'text': [779]})]
کلفت
[(125, {'text': [780]}), (147, {'text': [1954]})]
عقد
[(125, {'text': [783]}), (133, {'text': [76]})]
آورده_بود
[(125, {'text': [785]})]
ببیند
[(125, {'text': [802]})]
شغر
[(125, {'text': [822]})]
لحظات
[(125, {'text': [830]})]
آرمید
[(125, {'text': [842]})]
فراق
[(125, {'text': 

زانکه
[(130, {'text': [845]})]
برویاند
[(130, {'text': [848]})]
حدفاصل
[(130, {'text': [860]})]
دمساز
[(130, {'text': [870, 884]})]
روزن
[(130, {'text': [876]})]
می‌شنوند
[(130, {'text': [879]}), (132, {'text': [725]})]
خود‌گر
[(130, {'text': [885]})]
جفتم
[(130, {'text': [886]})]
گفتنی
[(130, {'text': [890]})]
گفتم
[(130, {'text': [891]})]
متشابه
[(130, {'text': [901, 910]}), (165, {'text': [52]})]
تاویلند
[(130, {'text': [920]})]
قصص
[(130, {'text': [928]})]
بیهش
[(130, {'text': [929]})]
خاصگ
[(130, {'text': [930]})]
اشاره‌اس
[(130, {'text': [935]})]
بیهو
[(130, {'text': [937]})]
هیب
[(130, {'text': [941]})]
تاویل
[(130, {'text': [949]})]
نشده‌اند
[(130, {'text': [955]}), (167, {'text': [817]})]
کاره
[(130, {'text': [961]})]
خام
[(130, {'text': [970, 1365]})]
شمس‌الدین
[(130, {'text': [987]}), (132, {'text': [275]})]
محشور
[(130, {'text': [1005]})]
بازگشته‌اس
[(130, {'text': [1025]})]
واجب
[(130, {'text': [1029]}), (162, {'text': [4098]})]
رمز
[(130, {'text': [1036]})]
انعا
[(130, {'

۱۹۶۴
[(147, {'text': [2907]})]
کوبریک
[(147, {'text': [2934]})]
مسنجر
[(148, {'text': [14, 1278]})]
مبدا
[(148, {'text': [16]})]
۴۶۶
[(148, {'text': [47]})]
۳۰۷
[(148, {'text': [53]})]
۳۸۷
[(148, {'text': [58]})]
۲۰۵
[(148, {'text': [62]})]
۸۷
[(148, {'text': [64, 107]})]
۹۶۹
[(148, {'text': [66]})]
۲۴۰
[(148, {'text': [70]})]
۸۸
[(148, {'text': [76]})]
۰۰۵
[(148, {'text': [110]})]
۳۳۱
[(148, {'text': [118]})]
۱۲۴
[(148, {'text': [122]})]
۱۷۴
[(148, {'text': [126]})]
۷۹۶
[(148, {'text': [128]})]
۱٫۰
[(148, {'text': [138]})]
۳۸۲۹
[(148, {'text': [194]})]
۰۸۳
[(148, {'text': [209]})]
۰۵۴
[(148, {'text': [213]})]
۳۰۲۲
[(148, {'text': [217]})]
۰۵۵
[(148, {'text': [220]})]
۵٫
[(148, {'text': [223]})]
۴۲۷
[(148, {'text': [224]})]
۴٫
[(148, {'text': [237]})]
۱۴۰۷
[(148, {'text': [245]})]
۸۹۲
[(148, {'text': [253]})]
۰٫۱′
[(148, {'text': [258]})]
۷۱۰
[(148, {'text': [276]})]
۷۱۴
[(148, {'text': [278]})]
۰۱
[(148, {'text': [293]})]
۱۱۹
[(148, {'text': [302]})]
۱۰۶
[(148, {'text': [305]})]
−۱٫۹


[(162, {'text': [3017]})]
سنگسار
[(162, {'text': [3019]})]
مخدر
[(162, {'text': [3027]})]
لواط
[(162, {'text': [3029]})]
محکومین
[(162, {'text': [3052, 3070]})]
تیربار
[(162, {'text': [3054]})]
بریدن
[(162, {'text': [3073]})]
گردن‌زده‌شدن
[(162, {'text': [3074]})]
murderer…
[(162, {'text': [3079]})]
میهمانی
[(162, {'text': [3087]})]
جداس
[(162, {'text': [3093]})]
قانونی‌شدن
[(162, {'text': [3124]})]
بلوغ
[(162, {'text': [3144, 3742]})]
رسیده_باشد
[(162, {'text': [3146]})]
نرسیده_اس
[(162, {'text': [3182]})]
زلفه
[(162, {'text': [3220]})]
به‌کارگیر
[(162, {'text': [3238]})]
بی‌گانه
[(162, {'text': [3240]})]
راننده
[(162, {'text': [3242]})]
آلمانی‌الاصل
[(162, {'text': [3260]})]
نادیده
[(162, {'text': [3264]})]
توهین
[(162, {'text': [3281]})]
روبند
[(162, {'text': [3327, 3816, 3976, 4067]})]
رأی‌گیر
[(162, {'text': [3348, 3387]})]
گزین
[(162, {'text': [3350, 3384]})]
هیاج
[(162, {'text': [3372]})]
الزین
[(162, {'text': [3373]})]
آموزشگاه
[(162, {'text': [3426, 3746, 3870]})]
استثنائ
[(16

## بخش سوم: فشرده سازی نمایه ها

<div dir="rtl">حال به سراغ بخش سه می رویم و تابع variable byte را می سازیم. به این صورت که ابتدا gap ها شناسایی میشوند و سپس هر کدام را به variable byte تبدیل میکنیم و در انتها همه ی gap هایی که در یک بخش بودند را به هم می چسبانیم.</div>

In [64]:
def encode_number(number):
    bytes_list = []
    while True:
        bytes_list.insert(0, number % 128)
        if number < 128:
            break
        number = number // 128
    bytes_list[-1] += 128
    return pack('%dB' % len(bytes_list), *bytes_list)
def encode(numbers):
    bytes_list = []
    for number in numbers:
        bytes_list.append(encode_number(number))
    return b"".join(bytes_list)
def variable_byte(posting):
    gaps = [posting[0]]
    binaries = []
    for i in range(len(posting)-1):
        gaps += [posting[i+1] - posting[i]]
    byte_array = encode(gaps)
    return byte_array

<div dir="rtl">حال مانند بخش variable byte عمل میکنیم با این تفاوت که این بار به جای روش variable byte از gamma code استفاده کرده ایم:</div>

In [65]:
def encode_gamma(number):
    code =""
    binary = bin(number)
    binary = binary[2:]
    offset = binary[1:]
    length = ""
    for j in range(len(offset)):
        length +="1"
    length += "0"
    code += length + offset
    number = int(code, base=2)
    l = 1
    while number >128:
        number = number // 128
        l += 1
    return number.to_bytes(l, 'big')
def encode(numbers):
    bytes_list = []
    for number in numbers:
        bytes_list.append(encode_gamma(number))
    return b"".join(bytes_list)
def gamma_code(posting):
    gaps = [posting[0]]
    code =""
    for i in range(len(posting)-1):
        gaps += [posting[i+1] - posting[i]]
    byte_array = encode(gaps)
    return byte_array

### تست بخش سوم

<div dir='rtl'>
    ابتدا پیاده سازی این کد ها را روی مجموعه نمایه های ساخته شده از بخش قبل نمایش میدهیم.
    </div>

In [67]:
print("The gamma code of the postings are:")
gamma_compressed_positions = {}
for word in positions:
    gamma_compressed_positions[word] = []
    for doc in positions[word]:
        docid = doc[0]
        doc_pos = {}
        if 'title' in doc[1].keys():
            title_positions = doc[1].get('title')
            doc_pos['title'] = variable_byte(title_positions)
        if 'text' in doc[1].keys():
            text_positions = doc[1].get('text')
            doc_pos['text'] = variable_byte(text_positions)
        gamma_compressed_positions[word].append((docid, doc_pos))
print(gamma_compressed_positions)

The gamma code of the postings are:
{'باز': [(0, {'title': b'\x00', 'text': b'\x00\x0f\x04s\x18\x04'}), (12, {'text': b'\x00\x00\x7f'}), (16, {'text': b'\x00\x00\x1f'}), (19, {'text': b'\x00\x00\x7f'}), (25, {'text': b'\x00\x00\x1f\x00?\x00\x00\x1f\x00\x00\x1f'}), (29, {'text': b'\x00\x00\x1f'}), (30, {'text': b'\x00\x00\x07\x00\x00\x07'}), (36, {'text': b'\x00\x00\x07\x00\x00\x07\x00\x00\x00\x0f\x00\x00\x00\x03\x00\x00\x7f\x00\x00\x07'}), (39, {'text': b'\x00\x00\x00\x03\x00\x00\x07'}), (40, {'text': b'\x00\x00\x07'}), (42, {'text': b'\x00\x00\x07\x00\x00\x07\x00\x00\x01\x05'}), (44, {'text': b'\x00\x00\x00\x03'}), (45, {'text': b'\x00\x0f'}), (47, {'text': b'\x00\x00\x01'}), (52, {'text': b'\x00\x00\x1f'}), (54, {'text': b'\x00\x00\x01'}), (56, {'text': b'\x00\x0f\x00\x00\x01\x00\x00\x1f\x00?'}), (64, {'text': b'\x00\x00\x1f\x00\x00\x07'}), (65, {'text': b'\x00\x00\x7f\x00\x00\x7f'}), (71, {'text': b'\x00\x00\x00\x03'}), (72, {'text': b'\x00\x00\x01\x00\x00\x1f'}), (112, {'text': b'\

<div dir='rtl'>
در این قسمت میزان حافظه ی اشغال شده در حالت فشرده نشده و فشرده شده را نمایش میدهیم
<br>
برای ذخیره سازی و لود کردن فایل نمایه ها از دیسک ار دو تابع saver و loaderبخش دوم استفاده میکنیم.
</div>

In [68]:
positional_index_saver(compressed_positions, 'vbc_compressed_index.pickle')
positional_index_saver(gamma_compressed_positions, 'gamma_compressed_index.pickle')
print('the size of indexes before compression:')
print(os.stat('positional_index.pickle').st_size)
print('the size of indexes after compression with variable byte code:')
print(os.stat('vbc_compressed_index.pickle').st_size)
print('the size of indexes after compression with gamma code:')
print(os.stat('gamma_compressed_index.pickle').st_size)

the size of indexes before compression:
1214727
the size of indexes after compression with variable byte code:
1161138
the size of indexes after compression with gamma code:
1161138


In [81]:
#decoding the file in part3
def vb_decode(bytestream):
    n = 0
    numbers = []
    bytestream = unpack('%dB' % len(bytestream), bytestream)
    for byte in bytestream:
        if byte < 128:
            n = 128 * n + byte
        else:
            n = 128 * n + (byte - 128)
        numbers.append(n)
        n = 0
    return numbers
vb_encoded_positions = positional_index_loader('vbc_compressed_index.pickle')
vb_encoded_positions = positional_index_loader('vbc_compressed_index.pickle')
print(vb_encoded_positions.get('باز'))
decompressed_positions = {}
for word in vb_encoded_positions:
    decompressed_positions[word] = []
    for doc in vb_encoded_positions[word]:
        docid = doc[0]
        doc_pos = {}
        if 'title' in doc[1].keys():
            title_positions = doc[1].get('title')
            gaps= vb_decode(title_positions)
            for i in range(len(gaps) - 1):
                 gaps[i+1] += gaps[i]
            doc_pos['title'] = gaps
            
        if 'text' in doc[1].keys():
            text_positions = doc[1].get('text')
            gaps= vb_decode(text_positions)
            for i in range(len(gaps) - 1):
                 gaps[i+1] += gaps[i]
            doc_pos['text'] = gaps
        decompressed_positions[word].append((docid, doc_pos))
print('the resault of decompression:')
print(decompressed_positions.get('باز'))
print("compared with the main one:")
print(positions.get('باز'))
positions = decompressed_positions

[(0, {'title': b'\x00', 'text': b'\x00\x0f\x04s\x18\x04'}), (12, {'text': b'\x00\x00\x7f'}), (16, {'text': b'\x00\x00\x1f'}), (19, {'text': b'\x00\x00\x7f'}), (25, {'text': b'\x00\x00\x1f\x00?\x00\x00\x1f\x00\x00\x1f'}), (29, {'text': b'\x00\x00\x1f'}), (30, {'text': b'\x00\x00\x07\x00\x00\x07'}), (36, {'text': b'\x00\x00\x07\x00\x00\x07\x00\x00\x00\x0f\x00\x00\x00\x03\x00\x00\x7f\x00\x00\x07'}), (39, {'text': b'\x00\x00\x00\x03\x00\x00\x07'}), (40, {'text': b'\x00\x00\x07'}), (42, {'text': b'\x00\x00\x07\x00\x00\x07\x00\x00\x01\x05'}), (44, {'text': b'\x00\x00\x00\x03'}), (45, {'text': b'\x00\x0f'}), (47, {'text': b'\x00\x00\x01'}), (52, {'text': b'\x00\x00\x1f'}), (54, {'text': b'\x00\x00\x01'}), (56, {'text': b'\x00\x0f\x00\x00\x01\x00\x00\x1f\x00?'}), (64, {'text': b'\x00\x00\x1f\x00\x00\x07'}), (65, {'text': b'\x00\x00\x7f\x00\x00\x7f'}), (71, {'text': b'\x00\x00\x00\x03'}), (72, {'text': b'\x00\x00\x01\x00\x00\x1f'}), (112, {'text': b'\x00\x00\x7f'}), (125, {'text': b'\x00\x00\x1

 ## بخش چهارم: اصلاح پرسمان

<div dir="rtl">
این تابع، با گرفتن دو لیست ازbigram ها، فاصله ی جاکارد آن دو را محاسبه میکند. 
فاصله ی جاکارد برابر با حاصل تقسیم اندازه ی اشتراک دو مجموعه بر اجتماع آن هاست.
</div>

In [82]:
def jaccard(list1, list2):
    intersection = len((set(list1).intersection(list2)))
    union = (len(list1) + len(list2)) - intersection
    return float(intersection / union)

<div dir="rtl">
تابع زیر با دریافت کوئری کاربر و همین طور مجموعه ای از تمام لغات به کار رفته در متون، تک‌تک لغات را با کوئری سنجیده و در نهایت یک دیکشنری حاوی لغات مختلف به همراه فاصله ی جاکارد هر کدام با کوئری را برمی‌گرداند که به صورت نزولی هم مرتب شده است. (کلمات مربوط تر، در ابتدای دیکشنری آمده اند.)
</div>

In [83]:
def find_relevance_of_words(query, all_words):
    resault = {}
    q = list(bigram_dictionary_maker([[query]], [False]).keys())
    for word in all_words:
        resault[word] = jaccard(q, list(bigram_dictionary_maker([[word]], [False]).keys()))
        
    return dict(sorted(resault.items(), key=lambda x: x[1], reverse=True))

### تست بخش چهارم

<div dir="rtl">
در این جا می‌خواهیم نزدیک ترین کلمات به کوئری اشتباه «جمهیت» را پیدا کنیم.
</div>

In [84]:
rel = find_relevance_of_words('جمهیت', positions.keys())
print("final persian resault: ")
related_word = []
count = 0
for word in rel:
    if count <= 50:
        related_word.append(word)
related_word

final persian resault: 


['جمعیت',
 'جمهور',
 'تاهیت',
 'جنایت',
 'جنسیت',
 'جمهوری',
 'جماهیر',
 'پرجمعیت',
 'جمع',
 'جهت',
 'گیت',
 'سیت',
 'بیت',
 'جمل',
 'جمله',
 'بریت',
 'هیتی',
 'جمعا',
 'مهیا',
 'جموس',
 'جمیع',
 'جامه',
 'جمعه',
 'مهلت',
 'جمال',
 'هویت',
 'ملیت',
 'مهیج',
 'جماع',
 'مهین',
 'دایت',
 'جملگ',
 'کمیت',
 'مزیت',
 'مسیت',
 'جمعیت\u200cشناس',
 'جمهوریخواه',
 'مهارت',
 'اقلیت',
 'ترجمه',
 'روایت',
 'تربیت',
 'شخصیت',
 'وائیت',
 'ولایت',
 'حکایت',
 'مدنیت',
 'امنیت',
 'حمایت',
 'جریمه',
 'جمشید',
 'جمعور',
 'جمهوری\u200cخواه',
 'هائیت',
 'ذهنیت',
 'اهمیت',
 'آرمیت',
 'جیبوت',
 'وضعیت',
 'موفقیت',
 'پایتخت',
 'فعالیت',
 'حاکمیت',
 'موقعیت',
 'مدیریت',
 'قابلیت',
 'گرافیت',
 'ترینیت',
 'مهراهی',
 'جمعبند',
 'جمع\u200cآور',
 'آناهیتا',
 'اوگاریت',
 'کانکریت',
 'نارضایت',
 'محبوبیت',
 'محدودیت',
 'مسئولیت',
 'وب\u200cسایت',
 'مأموریت',
 'ماموریت',
 'پارازیت',
 'مارکسیسیت',
 'بی\u200cاهمیت',
 'جمشیدپور',
 'صهیونیست',
 'جمله\u200cاند',
 'ج',
 'ت',
 'رول\u200cاسکیت',
 'رئیس\u200cجمهور',
 'نیمه\u200

<div dir="rtl">
در نهایت با استفاده از الگوریتم edit distance بهترین کلمه ای را که میتواند جایگزین کلمه ی اشتباه موجود در query باشد را از میان کلمات انتخاب شده از معیار جاکارد انتخاب می کنیم و به عنوان خروجی می دهیم:
</div>

In [85]:
def edit_distance(words, query_word):
    distance = []
    for word in words:
        matrix = [[0 for i in range(len(word)+1)] for j in range(len(query_word)+1)]
        for i in range(len(word)+1):
            matrix[0][i] = i
        for i in range(len(query_word)+1):
            matrix[i][0] = i
        for i in range(1,len(query_word)+1):
            for j in range(1,len(word)+1):
                scores = []
                scores += [matrix[i-1][j] +1]
                scores += [matrix[i][j-1] +1]
                if word[j-1]==query_word[i-1]:
                    scores+= [matrix[i-1][j-1]]
                else:
                    scores += [matrix[i-1][j-1]+1]
                matrix[i][j] = min(scores)
        distance += [matrix[len(query_word)][len(word)]]
    choosen_word = words[distance.index(min(distance))]
    return choosen_word

In [86]:
edit_distance(related_word, 'جمهیت')

'جمعیت'

## بخش پنجم: جستجو و بازیابی اسناد

<div dir='rtl'>
    این تابع معیار idf را برای هر کلمه محاسبه میکند.
    </div>

In [87]:
def idf_calculator(positional_index, term, n):
    posting = positional_index.get(term)
    if(posting != None):
        df = len(posting)
        idf = math.log(n/df)
    else:
        return 0
    return idf

<div dir='rtl'>
    تابع زیر مشابه تابع بخش اول پردازش های اولیه را روی متن انجام میدهد.
    تابع بخش اول برای فایل های دارای ساختار xml طراحی شده بود به همین خاطر این تابع را مینویسیم تا بتوانیم ورودی های رشته ای را هم پردازش کنیم.
    </div>

In [88]:
def prepare_query(query, PUNC_FLAG, STEM_FLAG, STWD_FLAG):
    #removing all puctuations
    if(PUNC_FLAG):
        query = re.sub(r"[\[,.;:\-@#}?؟{٪٬*!)%’(&$<_>/'»«|+=.\]]+\ *", " ", query)

    #removing all english letters and numbers
    new_query = ""
    for i in query.split(' '):
        if i.isascii() == False and i.isdigit() == False:
            new_query += i + ' '

    query = new_query
    normalizer = Normalizer()
    query = normalizer.normalize(query)
    tokenizer = WordTokenizer()
    query = tokenizer.tokenize(query)
    new_query = []
    if(STEM_FLAG):
        stemmer = Stemmer()
        for t in query:
            t1 = stemmer.stem(t)
            new_query += [t1]
    else:
        for t in query:
            new_query += [t]
    
    if(STWD_FLAG):
        with open('retrieved_stopwords.pickle', 'rb') as handle:
            stop_words = pickle.load(handle)
        query = [w for w in new_query if not w in stop_words]

    return query

In [89]:
prepare_query("جمعیت کشور‌ها‌ی مختلف", True,True, False)

['جمعیت', 'کشور\u200cها\u200cی', 'مختلف']

<div dir='rtl'>
این تابع می آید نرم دوم وزن کلمات داخل یک مستند را محاسبه میکند. و این مقدار در واقع همان normalizing factor است.
</div>

In [90]:
def cosine_normalizing_factor(positional_index, N):
    M = len(positional_index.items())
    text_vector = [0 for i in range(N)]
    title_vector = [0 for i in range(N)]
    for key, value in positional_index.items():
        for doc in value:
            if 'text' in doc[1].keys():
                tf = 1 + math.log(len(doc[1].get('text')))
            else: tf = 0
            text_vector[doc[0]] += tf**2
            if 'title' in doc[1].keys():
                tf = 1 + math.log(len(doc[1].get('title')))
            else: tf = 0
            title_vector[doc[0]] += tf**2
    text_vector = [math.sqrt(v) for v in text_vector]
    title_vector = [math.sqrt(v) for v in title_vector]
    return text_vector, title_vector
        
text, title = cosine_normalizing_factor(positions, len(main_docs))

<div dir='rtl'>
میدانیم که به ازای کلماتی که داخل کوئری نیستند امتیاز نهایی صفر میشود چرا که از حاصلضرب نقطه ای بردار ها بدست می آید و اگر در یکی از این دو بردار به ازای آن کلمه صفر باشد در کل صفر است.
    <br>
    به همین خاطر تایع زیر مقدار بردار ها را برای کلمات داخل کوئری حساب میکند و در نهایت ده مستند با امتیاز بیشتر را برمیگرداند
</div>

In [79]:
def tfidfweighter(query, positional_index, n):
    text, title = cosine_normalizing_factor(positional_index, n)
    vectors = {}
    #finding documents with their scores for the words of query
    for i in range(len(query)):
        posting = positional_index.get(query[i])
        if(posting != None):
            for doc in posting:
                if 'title' in doc[1].keys():
                    title_tf = 1 + math.log(len(doc[1].get('title')))
                else: title_tf = 0
                if 'text' in doc[1].keys():
                    text_tf = 1 + math.log(len(doc[1].get('text')))
                else: text_tf = 0
                if doc[0] not in vectors.keys():
                    vectors[doc[0]] = [0 for i in range(len(query))]
                if(title[doc[0]] == 0 ):
                    vectors[doc[0]][i] = text_tf/text[doc[0]]
                elif (text[doc[0]] == 0) :
                    vectors[doc[0]][i] = title_tf/title[doc[0]]
                else:
                    vectors[doc[0]][i] = text_tf/text[doc[0]] + title_tf/title[doc[0]]   
    #calculating the weights of query
    weights = [0 for i in range(len(query))]
    for i in range(len(query)):
        tf = 1 + math.log(query.count(query[i]))
        idf = idf_calculator(positional_index, query[i], n)
        weights[i] = tf * idf
    normalizer = np.linalg.norm(weights)
    weights = [w/normalizer for w in weights]
    ranks = []
    for docid, value in vectors.items():
        pr = np.dot(weights, value)
        ranks.append((pr, docid))
    ranks = sorted(ranks, reverse=True)
    return ranks[:10]

In [91]:
n = len(main_docs)
tfidfweighter(['باز','فکر'], positions, len(main_docs))

[(1.3157711661485907, 0),
 (0.12452360976630562, 140),
 (0.07728992084112064, 45),
 (0.05116010711057979, 125),
 (0.04462484378730646, 130),
 (0.042790101437271494, 54),
 (0.03889262145483717, 162),
 (0.0360311592256952, 59),
 (0.034688246690141596, 42),
 (0.03396708821067758, 149)]

### تست بخش پنجم و نهایی

In [95]:
#final ui
query = input("Type the query:")
if(input("Type the options for processing query.(it is recommended to enter the same options as the main text preprocessing.) Do you want stemming?[T/F]") == 'T'): 
    stfl = True
else: stfl = False
if(input("Do you want stop word removal?[T/F]") == 'T'): 
    stwdfl = True
else: stwdfl = False
if(input("Do you want punctuation removal?[T/F]") == 'T'): 
    puncfl = True
else: puncfl = False
query_terms = prepare_query(query, puncfl, stfl, stwdfl)
true_word = []
tokens = positions.keys()
for word in query_terms:
    if word not in tokens:
        wrong_word = word
        dic = find_relevance_of_words(word , tokens)
        related_word =[]
        count = 0
        for i in dic:
            if count<=50:
                related_word += [i]

            else:
                break
            count+=1
        true_word += [edit_distance(related_word , wrong_word)]
    else:
        true_word += [word]
print(true_word)
for i in range(len(true_word)):
    query_corrected = query.replace(query_terms[i],true_word[i])
print("Did you mean: " + query_corrected + "?")
correct = input("Y/N: ")
if(correct == 'Y'):
    query = query_corrected
    print("The 10 best results of "+ query +" are:")
    tf_idf=tfidfweighter(true_word, positions,len(main_docs))
    for i in range(len(tf_idf)):
        print(tf_idf[i][1])
else:
    print("The 10 best results of "+query+" are:")
    tf_idf=tfidfweighter(query_terms, positions, len(main_docs))
    for i in range(len(tf_idf)):
        print(tf_idf[i][1])
print("Please enter the documentID that you want to see:")
doc = int(input())
print(main_docs[doc])

Type the query:تخت جمشید
Type the options for processing query.(it is recommended to enter the same options as the main text preprocessing.) Do you want stemming?[T/F]T
Do you want stop word removal?[T/F]T
Do you want punctuation removal?[T/F]T
['تخ', 'جمشید']
Did you mean: تخت جمشید?
Y/N: Y
The 10 best results of تخت جمشید are:
52
53
146
56
41
16
30
132
130
12
Please enter the documentID that you want to see:
52
تخت جمشید 
نحش سخ جعبه اطلاعات میراث جهانی یونسکو
 نام تخت جمشید
 ۱
 
ردیف راست سخ سنگ‌نبشته اردشیر یکم در کاخ ه سنگ‌نبشته اردشیر یکم در کاخ ه سخ 
ردیف چپ سخ 
نمایی کلی از کاخ آپادانای تخت جمشید سخ 
ردیف راست سخ 
سنگ‌نگاره مردان ماد در حال قدم زدن در کاخ سه‌در سخ 
ردیف چپ سخ 
نمایی کلی از کاخ صدستون سخ 
ردیف راست سخ 
گاوان دروازه‌بان در کاخ دروازه کشورها سخ 
ردیف چپ سخ کتیبه‌های پی‌بنای کاخ آپادانا تخت جمشید یکی از هشت کتیبه پی‌بنای کاخ آپادانا تخت جمشید سخ 
ردیف راست سخ 
هدیه‌آوران لودیه در پلکان‌های کاخ آپادانای تخت جمشید سخ 
ردیف چپ سخ 
نبرد گاو و شیر، نمادی از نوروز زرتشتی